# Setting up our imported libraries.

In [1]:
from functools import reduce
import numpy as np
from keras.models import Sequential
from keras.layers import Dense
from os.path import join

Using TensorFlow backend.


# Function definitions

In [20]:
# Used to format our input binary state.

def format_input(acc, elem):
    hex_elem = (elem - (elem >> 4 << 4))
    for x in range(16):
        if x == hex_elem:
            acc.append(1)
        else:
            acc.append(0)
    hex_elem = (elem >> 4) % 16
    for x in range(16):
        if x == hex_elem:
            acc.append(1)
        else:
            acc.append(0)
    return acc

# Calculate Manhattan distance between two points.

def man_dist(x, y):
    for a, b in zip(x, y):
        a_one, a_two = x
        b_one, b_two = y
    
    return (abs(a_one - b_one) + abs(a_two - b_two))
            
# Calculate Manhattan distance between each set of two points in a list.
    
def man_dist_state(x, y):
    return sum(man_dist(a, b) for a, b in zip(x, y))

# Used to format the positions we parsed from our binary input.

def format_pos(acc, elem):
    hex_elem = (elem[1] - (elem[1] >> 4 << 4))
    if hex_elem == 0:
        acc.append((hex_elem, (3,3)))
    else:
        acc.append((hex_elem, ((15 - ((elem[0]) * 2)) % 4,int((15 - ((elem[0]) * 2)) / 4))))
    hex_elem = (elem[1] >> 4) % 16
    if hex_elem == 0:
        acc.append((hex_elem, (3,3)))
    else:
        acc.append((hex_elem, ((15 - ((elem[0]) * 2 + 1)) % 4,int((15 - ((elem[0]) * 2 + 1)) / 4))))
    
    return acc

# The title of this function is slightly misleading.
# I'm simply generating a list of positions that each
# puzzle piece in the current parsed state SHOULD be at.
# I organize this in order of the pieces as they were
# parsed so the two lists line up perfectly.

def generate_pos(acc, elem):
    if(elem[0] == 0):
        acc.append((3,3))
    else:
        acc.append((((elem[0] - 1) % 4), (int((elem[0] - 1)/4))))
    
    return acc

# Used to format our ending Manhattan distance into a format
# that can be compared with our 29 output neurons.

def format_man_dist(elem):
    acc = []
    for x in range(28, -1, -1):
        if x == elem:
            acc.append(1)
        else:
            acc.append(0)
    return acc


# Parsing input

## Creating Target data

For this cell, I wanted to clearly explain how the script past this point works. Since I don't want to parse all of the binary states from each file that I'm going to use all at once and hold them in RAM, this instead parses 1 binary state at a time (8 bytes, meaning 64 bits, and we ignore the 1st 4 bits), does the calculations and input formatting needed, and appends the end result per state to a list to be used later.

In [21]:
target = []

for i in range(29):
    filename = join('data', str(i) + '.bin')
    
    # Debugging to print the current file from which states are being parsed.
    #print(i)
    temp = []
    
    with open(filename, 'rb') as f:
        data = f.read(8)
        counter = 0

        while(data and counter < 1000):
            temp.append(format_man_dist(i))
            
            data = f.read(8)
            counter += 1
        
        target.append(temp)
            
#print(target[28][500])

# Parsing and Training the neural network

### Setting up the neural network

Before we run our training/parsing, we need to make sure Keras has configured the neural network properly to our specifications.

In [22]:
# Sets up a Sequential model, Sequential is all
# that should need to be used for this project,
# considering that it will only be dealing with
# a linear stack of layers of neurons.

model = Sequential()

# Adding layers to the model.

model.add(Dense(units=240, activation='tanh', input_dim=240))
model.add(Dense(units=120, activation='tanh'))
model.add(Dense(units=60, activation='tanh'))
model.add(Dense(units=29, activation='sigmoid'))

# Configure the learning process.

model.compile(optimizer='sgd',
             loss='mean_squared_error',
             metrics=['accuracy'])

### Training the neural network

Again, this part has the parsing and training in hand, since as we parse and format the states from our file input, we feed those batches to our neural network to train with.

In [23]:
for i in range(29):
    filename = join('data', str(i) + '.bin')
    
    # Debugging to print the current file from which states are being parsed.
    print(i)
    
    with open(filename, 'rb') as f:
        data = f.read(8)
        counter = 0
        training = []

        while(data and counter < 1000):
            bin_data = reduce(format_input, list(data), [])
            bin_data.reverse()
            bin_data = bin_data[16:]
            
            training.append(bin_data)

            data = f.read(8)
            counter += 1

            #print(training[0])
    # Train the network.

    model.fit(np.array(training), np.array(target[i]), epochs=5, batch_size=100)
    #model.train_on_batch(np.array(temp), np.array(target))

0
Epoch 1/5
1/1 [==============================] - 0s 151ms/step - loss: 0.2526 - acc: 0.0000e+00
Epoch 2/5
1/1 [==============================] - 0s 2ms/step - loss: 0.2512 - acc: 0.0000e+00
Epoch 3/5
1/1 [==============================] - 0s 2ms/step - loss: 0.2499 - acc: 0.0000e+00
Epoch 4/5
1/1 [==============================] - 0s 2ms/step - loss: 0.2486 - acc: 0.0000e+00
Epoch 5/5
1/1 [==============================] - 0s 2ms/step - loss: 0.2473 - acc: 0.0000e+00
1
Epoch 1/5
2/2 [==============================] - 0s 894us/step - loss: 0.2514 - acc: 0.0000e+00
Epoch 2/5
2/2 [==============================] - 0s 852us/step - loss: 0.2504 - acc: 0.0000e+00
Epoch 3/5
2/2 [==============================] - 0s 866us/step - loss: 0.2494 - acc: 0.0000e+00
Epoch 4/5
2/2 [==============================] - 0s 834us/step - loss: 0.2484 - acc: 0.0000e+00
Epoch 5/5
2/2 [==============================] - 0s 809us/step - loss: 0.2474 - acc: 0.0000e+00
2
Epoch 1/5
4/4 [===========================

1000/1000 [==============================] - 0s 17us/step - loss: 0.1249 - acc: 0.0090
Epoch 5/5
1000/1000 [==============================] - 0s 17us/step - loss: 0.1221 - acc: 0.0190
17
Epoch 1/5
1000/1000 [==============================] - 0s 14us/step - loss: 0.1190 - acc: 0.0770
Epoch 2/5
1000/1000 [==============================] - 0s 17us/step - loss: 0.1162 - acc: 0.1200
Epoch 3/5
1000/1000 [==============================] - 0s 16us/step - loss: 0.1135 - acc: 0.1700
Epoch 4/5
1000/1000 [==============================] - 0s 17us/step - loss: 0.1108 - acc: 0.2220
Epoch 5/5
1000/1000 [==============================] - 0s 20us/step - loss: 0.1082 - acc: 0.2810
18
Epoch 1/5
1000/1000 [==============================] - 0s 15us/step - loss: 0.1188 - acc: 0.0000e+00
Epoch 2/5
1000/1000 [==============================] - 0s 17us/step - loss: 0.1165 - acc: 0.0000e+00
Epoch 3/5
1000/1000 [==============================] - 0s 19us/step - loss: 0.1143 - acc: 0.0000e+00
Epoch 4/5
1000/1000 [=

# Testing the neural network

## Creating the testing target data

Similarly, here is a separate cell that just parses and creates the necessary target and testing arrays that we will need to test the neural network using Keras.

In [24]:
# Used for testing data

with open('data/18.bin', 'rb') as f:
    
    for i in range(1000):
        data = f.read(8)
        
    data = f.read(8)
    
    counter = 0
        
    testing = []
    
    testing_target = []
    
    while(data):
        bin_data = reduce(format_input, list(data), [])
        bin_data.reverse()
        bin_data = bin_data[16:]

        testing.append(bin_data)

        pos_data = reduce(format_pos, enumerate(list(data)), [])
        pos_data.reverse()
        pos_data = pos_data[1:]
        
        state_pos = []

        for p in pos_data:
            state_pos.append(p[1])
            
        testing_target_pos = reduce(generate_pos, pos_data, [])

        testing_target.append(format_man_dist(man_dist_state(state_pos, testing_target_pos)))
        
        counter += 1
        data = f.read(8)
        
#print(testing_target)

## Evaluating our test data

In [25]:
# Evaluate accuracy
    
loss_and_metrics = model.evaluate(np.array(testing),np.array(testing_target), batch_size=1000)
        
# Generating predictions:
    
predictions = model.predict(np.array(testing), batch_size=1000)

446342/446342 [==============================] - 1s 2us/step


In [42]:
for i in testing_target:
    print(np.argmax(i))

11
11
15
13
12
12
14
13
11
13
13
11
11
11
12
13
15
13
13
13
13
17
17
13
13
13
13
15
13
13
12
12
14
13
11
11
11
15
15
17
17
14
14
13
13
13
13
15
15
13
13
13
13
13
12
15
15
13
15
13
14
13
13
13
13
13
13
13
13
15
13
14
15
19
16
15
15
15
12
15
15
13
13
14
13
13
13
13
15
13
13
15
13
12
15
15
14
13
13
15
15
13
13
13
15
14
13
13
13
13
12
17
13
13
13
13
13
13
10
11
15
11
13
15
15
13
15
11
13
11
11
16
14
10
13
11
11
11
13
11
11
11
11
15
13
12
13
17
13
11
11
13
13
13
11
11
16
14
10
13
11
11
11
13
11
11
10
13
13
11
11
11
13
13
11
13
11
11
15
13
10
11
13
13
11
10
11
13
12
13
13
13
11
11
11
13
13
13
13
12
13
17
14
13
13
15
10
13
13
11
11
12
11
11
11
11
11
13
13
13
13
24
16
16
16
18
18
16
16
16
18
20
18
16
16
18
16
16
19
18
18
18
16
14
14
18
14
16
18
14
16
14
14
16
14
14
16
18
16
14
14
14
14
16
14
14
14
14
14
15
15
15
17
15
15
17
17
17
15
21
13
15
17
13
15
13
13
15
13
13
13
15
15
15
17
19
10
15
13
13
13
13
15
13
13
13
15
15
10
13
14
15
11
11
11
16
15
13
11
11
11
11
11
13
13
13
11
13
11
11
11
11
10
1

14
14
16
14
14
16
18
14
14
14
14
16
14
14
13
15
12
12
10
12
10
16
18
10
10
12
14
12
14
12
12
12
12
14
14
14
16
14
16
14
14
14
10
10
10
10
10
10
10
10
12
12
12
12
12
10
10
10
10
10
12
10
12
10
10
14
14
18
16
18
16
18
14
14
14
12
12
12
14
14
14
12
12
12
10
12
12
12
10
12
12
12
10
10
10
12
10
10
18
14
14
14
14
10
12
12
12
10
10
14
10
12
14
10
12
10
10
14
12
12
14
10
10
10
10
12
12
12
12
14
14
14
14
12
12
12
16
12
12
12
12
16
12
12
14
10
10
10
10
10
10
10
10
14
12
10
10
12
12
12
14
10
10
12
10
12
14
12
10
10
10
14
12
18
16
14
14
12
14
12
12
12
12
14
12
15
17
18
14
14
14
10
10
14
10
12
14
12
10
10
10
12
10
10
10
10
14
14
14
14
12
14
12
12
10
10
10
18
14
14
14
14
12
10
14
10
10
14
10
12
14
10
12
10
10
12
12
14
14
14
14
12
14
12
14
12
12
12
12
10
12
10
10
12
10
10
13
13
12
12
12
12
12
12
12
18
14
14
14
14
10
10
10
14
10
12
14
12
12
10
12
14
12
14
12
12
14
10
10
10
10
10
12
14
12
10
10
10
12
10
10
10
12
12
12
10
10
12
12
12
12
12
12
12
12
12
14
16
14
12
12
12
12
16
16
16
14
10
10
12
12
10
10
1

11
11
12
13
11
11
11
11
11
11
13
13
13
11
11
11
11
11
11
20
17
17
17
17
17
17
17
17
17
17
22
17
15
17
19
15
15
15
15
17
15
15
16
15
15
15
15
15
15
17
15
15
15
15
15
15
15
16
15
13
15
13
13
13
13
16
17
19
15
17
16
15
15
15
15
15
15
15
15
15
19
17
17
17
17
17
17
16
16
12
13
15
13
13
15
13
13
15
13
13
14
13
15
13
15
13
13
13
15
13
13
12
13
15
15
14
15
17
15
15
15
15
19
17
15
15
15
15
15
15
15
14
13
13
15
13
15
13
14
13
13
13
13
15
13
17
15
13
13
15
18
14
14
14
14
16
18
16
16
16
14
14
15
15
15
11
11
14
13
15
17
13
15
13
13
15
13
13
13
11
11
11
13
11
11
11
11
11
12
13
17
15
12
11
13
11
11
11
13
11
11
13
11
11
13
11
11
11
13
11
11
15
15
16
15
13
13
15
13
15
13
15
11
11
13
12
11
11
11
11
11
10
11
15
13
13
17
15
15
13
13
15
15
10
11
11
13
13
12
13
15
10
11
11
11
11
17
15
15
15
13
13
15
13
13
15
15
13
13
15
13
13
13
12
13
17
15
15
12
11
11
13
11
11
11
13
11
12
11
13
11
11
11
13
11
11
13
11
11
13
13
13
14
14
10
11
15
13
13
13
11
11
12
13
17
15
13
11
11
11
13
11
11
11
11
12
13
10
11
11
13
11
11
1

17
15
15
16
15
13
15
17
15
15
17
15
15
13
13
13
14
17
16
15
15
15
17
15
17
15
15
13
13
13
15
13
15
13
13
17
17
19
15
15
17
15
17
15
14
12
12
12
12
14
14
14
14
14
16
14
14
12
12
12
12
12
14
12
12
13
13
16
18
18
18
20
12
12
16
16
16
14
14
16
16
16
14
14
16
16
16
16
14
14
14
14
14
14
17
15
14
12
12
14
14
12
12
12
14
14
18
18
16
16
14
16
18
14
14
16
16
16
16
16
14
14
14
14
14
12
12
14
12
12
14
12
14
12
12
12
14
12
12
10
11
12
11
15
13
15
17
15
15
13
15
13
13
11
11
11
11
11
13
11
11
16
18
14
16
16
14
14
14
16
14
18
18
18
18
18
16
16
18
18
18
18
18
18
16
16
18
18
15
13
10
12
10
10
10
10
10
14
14
12
12
14
12
12
10
10
10
12
14
12
14
12
12
14
14
14
12
12
14
14
16
14
14
18
16
16
14
14
14
14
14
12
14
14
12
12
12
12
12
12
15
15
17
17
19
14
10
11
11
13
11
11
13
15
15
15
15
13
15
13
13
12
12
14
10
12
11
11
10
12
14
16
16
16
14
14
16
14
14
16
16
14
14
14
14
18
18
16
14
16
18
12
14
12
14
14
14
12
12
12
12
12
12
14
10
12
10
14
12
12
10
12
10
10
12
10
10
10
10
10
10
14
12
14
12
14
12
14
14
12
14
12
12
1

12
12
12
14
12
12
12
12
14
16
16
14
16
16
14
16
16
12
12
14
12
12
12
15
15
15
15
12
15
15
13
13
13
13
14
16
14
14
14
14
14
16
16
12
12
14
12
12
14
14
16
12
12
12
14
12
12
16
12
12
12
12
12
14
12
12
12
12
14
12
12
16
12
12
18
16
16
16
16
16
14
15
16
16
18
13
13
14
13
13
12
12
14
12
12
12
12
14
16
12
12
14
16
16
12
12
12
14
14
14
18
16
16
18
18
16
18
18
18
16
14
12
12
14
14
16
14
15
15
15
15
12
15
15
13
13
13
13
13
14
16
14
14
14
14
14
16
16
12
12
14
12
12
12
14
16
12
12
12
12
16
14
12
12
16
12
12
12
16
14
13
13
14
14
14
14
13
13
12
12
16
14
16
16
12
12
14
12
12
14
16
12
12
14
16
12
12
12
12
12
12
12
14
16
16
14
16
16
12
12
18
16
16
16
18
16
14
15
16
16
18
18
13
13
14
13
13
12
12
12
12
12
12
12
12
14
12
12
12
14
16
16
13
13
14
14
14
13
13
12
12
12
14
16
16
12
12
14
13
13
12
12
14
12
12
12
12
12
12
14
12
12
12
12
14
12
12
12
12
16
16
17
17
17
18
18
18
18
18
18
18
18
18
20
20
20
20
20
20
22
24
18
18
14
15
15
15
15
15
15
15
15
16
16
18
18
16
17
15
15
15
15
14
14
14
14
16
14
14
14
14
14
14
1

...

14
16
10
10
12
10
10
12
10
12
15
15
14
14
14
14
16
18
16
16
14
14
14
18
18
16
16
16
16
18
14
14
14
16
18
14
14
12
12
12
12
12
14
16
18
14
14
14
14
14
18
16
12
12
12
12
12
16
16
16
16
14
16
14
13
15
10
10
10
14
14
12
16
14
14
12
12
12
16
14
14
16
10
12
12
12
14
14
16
10
10
12
10
10
10
10
12
12
12
10
10
12
12
14
16
10
10
10
10
10
12
14
12
12
14
10
10
12
12
12
10
12
10
10
10
10
10
12
12
12
12
12
14
16
10
12
12
14
10
10
10
10
10
10
12
12
14
12
10
10
10
10
12
12
12
10
10
10
14
14
14
12
12
12
12
12
14
14
14
13
13
12
12
12
14
14
12
12
12
16
16
14
18
16
16
14
14
16
14
16
14
16
12
12
14
14
14
12
12
12
12
16
14
16
12
12
14
14
14
12
12
12
12
12
12
12
14
14
14
16
18
20
16
16
16
16
16
16
16
16
16
16
18
16
18
16
18
14
14
14
14
14
14
14
18
14
16
14
14
14
14
16
16
14
14
14
14
14
16
14
14
14
14
13
13
14
14
14
14
14
16
14
14
12
14
10
12
11
11
10
14
12
12
12
10
12
10
10
10
10
10
12
12
12
16
16
10
10
12
16
14
14
16
12
12
14
10
10
10
12
14
12
12
11
11
10
10
10
12
12
10
12
10
10
14
14
12
16
12
14
12
12
16
1

13
15
15
17
13
15
14
15
12
13
15
13
13
12
15
13
13
13
15
15
15
15
17
17
15
15
15
15
15
15
15
15
14
13
12
13
13
13
13
15
13
13
13
13
13
15
17
14
15
12
13
15
13
13
12
15
13
15
17
13
15
12
15
13
13
13
18
18
17
19
17
17
18
18
17
17
15
20
15
15
15
15
17
15
15
15
17
18
16
18
19
19
17
17
17
17
15
15
19
18
16
18
19
19
17
17
17
17
17
16
17
14
15
17
15
15
19
16
18
20
20
22
22
20
20
18
18
18
16
13
13
13
13
13
15
15
15
15
17
17
15
15
13
11
11
11
13
16
16
12
13
13
13
14
13
13
15
13
13
13
15
13
15
17
13
13
18
17
14
15
15
15
18
19
17
15
15
17
15
15
17
19
17
17
16
14
12
13
15
13
15
17
17
15
11
11
18
16
13
15
15
17
13
13
13
13
11
11
16
17
15
15
15
17
13
13
15
12
13
11
11
11
11
11
13
15
13
13
15
11
11
12
13
11
11
11
12
13
11
14
13
10
11
15
13
13
13
15
13
11
13
15
11
13
11
11
16
15
12
13
15
15
15
15
13
13
13
13
13
15
13
13
13
14
13
10
11
13
13
15
11
11
11
11
11
13
11
13
12
13
11
14
13
10
11
13
13
13
11
11
11
14
13
10
11
13
13
13
13
13
11
11
11
11
11
13
13
13
13
15
13
13
13
13
15
15
15
13
18
16
13
13
13
1

14
14
12
10
10
10
10
10
10
10
10
12
12
10
10
14
14
11
11
11
11
11
13
13
13
12
10
12
12
12
12
12
12
12
12
12
12
12
12
14
14
16
16
14
14
16
16
14
14
14
16
12
12
12
12
12
14
16
18
16
16
16
12
12
12
12
14
14
14
14
16
14
14
14
14
14
14
14
14
14
15
15
16
18
18
18
16
18
16
12
12
12
12
14
14
14
14
14
14
14
16
18
14
14
14
12
10
10
12
12
12
12
10
12
10
12
10
10
12
10
12
10
14
12
10
12
12
10
10
14
12
10
10
10
10
12
10
12
10
10
14
12
12
12
10
10
10
11
11
12
10
12
10
14
14
12
10
10
12
10
10
14
14
12
12
14
10
10
10
10
10
12
10
12
12
10
12
10
10
10
10
10
10
10
12
12
10
10
12
10
10
10
10
12
12
12
12
14
14
12
12
12
12
14
14
14
14
16
16
16
14
14
14
16
16
14
16
12
12
16
14
12
12
14
14
16
14
12
14
12
14
12
12
14
12
14
12
14
16
14
16
16
14
16
16
14
16
14
12
12
12
14
14
14
12
14
12
14
14
16
14
14
12
12
14
14
13
13
14
12
14
12
16
16
14
12
12
14
12
14
14
12
14
14
14
14
14
14
16
14
16
16
18
16
14
14
14
16
18
18
20
18
16
14
14
16
14
12
12
12
12
14
14
14
14
14
16
14
14
12
12
12
14
13
13
14
14
14
12
16
16
14
14
1

12
12
10
10
12
12
17
17
16
16
18
18
18
16
18
16
18
18
18
18
20
20
18
18
18
18
20
22
16
18
14
14
14
14
14
14
14
18
16
18
16
14
11
11
10
10
12
12
12
10
10
12
10
12
10
10
10
10
12
10
14
12
12
10
12
10
10
14
11
11
10
10
10
10
10
10
12
10
10
14
12
11
10
10
10
11
12
12
14
10
10
12
10
12
12
14
10
10
14
14
16
12
14
12
12
12
12
12
14
12
10
10
10
16
14
10
12
14
10
10
10
10
10
10
10
10
12
10
10
12
12
12
12
12
14
14
10
10
10
16
12
14
12
12
12
12
14
14
14
14
16
16
16
12
12
12
12
12
14
14
16
13
12
12
14
14
16
12
12
14
12
14
12
12
12
12
14
12
14
16
16
14
16
14
16
16
14
13
13
12
12
12
14
14
12
12
14
12
14
14
16
13
12
12
14
14
13
14
14
16
12
12
14
12
14
14
12
14
14
12
18
16
16
16
16
16
18
16
14
14
14
20
16
16
14
14
14
16
18
18
16
16
14
14
13
13
12
12
12
12
14
12
14
14
14
16
13
12
12
12
14
13
14
16
16
12
12
14
12
16
16
16
16
14
18
14
14
12
12
12
12
16
14
16
16
14
16
18
15
14
14
14
15
14
16
14
16
16
18
20
16
18
18
16
13
13
12
12
14
14
14
12
14
16
16
16
12
12
18
18
20
20
18
14
14
14
18
16
16
16
18
14
14
1

KeyboardInterrupt: 

In [49]:
output = []

for p in range(len(predictions)):
    if np.argmax(testing_target[p]) < 18:
        output.append(100*((18 - (28 - np.argmax(predictions[p]))) / (18 - np.argmax(testing_target[p]))))
    else:
        output.append(0)
    
#for i in range(len(output)):
#    print(output[i])

print(np.array(output).mean())

print(loss_and_metrics)

print(model.metrics_names)

124.38407816
[0.076097887326690691, 0.11989685069161862]
['loss', 'acc']


In [ ]:


with open('data/0.bin', 'rb') as f:
    data = f.read(8)
    counter = 0

    while(data):
        bin_data = reduce(format_input, list(data), [])
        bin_data.reverse()
        bin_data = bin_data[16:]

        print(counter)
        
        for i in range(int(len(bin_data)/240)):
            for x in range((i*16),(i*16) + 15):
                temp = []
                for y in range(16):
                    temp.append(bin_data[(x*16) + y])
        
        data = f.read(8)
        counter += 1

I'm going to need to calculate Manhattan Distances for each of the states at some point.

This website might be helpful for that formula:
https://heuristicswiki.wikispaces.com/Manhattan+Distance

In [ ]:

with open('data/0.bin', 'rb') as f:
    data = f.read(8)
    counter = 0
    
    while(data):
        pos_data = reduce(format_pos, enumerate(list(data)), [])
        pos_data.reverse()
        pos_data = pos_data[1:]
        
        state_pos = []
        
        for p in pos_data:
            state_pos.append(p[1])
        
        target_pos = reduce(generate_pos, pos_data, [])
        
        print(format_man_dist(man_dist_state(state_pos, target_pos)))
        
        data = f.read(8)
        counter += 1

In [ ]:
for i in range(29):
    filename = join('data', str(i) + '.bin')
    
    print(i)
    
    with open(filename, 'rb') as f:
        data = f.read(8)
        counter = 0
        
        temp = []
        target = []

        while(data and counter < 1000):
            bin_data = reduce(format_input, list(data), [])
            bin_data.reverse()
            bin_data = bin_data[16:]

            pos_data = reduce(format_pos, enumerate(list(data)), [])
            pos_data.reverse()

            state_pos = []

            for p in pos_data:
                state_pos.append(p[1])

            target_pos = reduce(generate_pos, pos_data, [])

            #for i in range(int(len(bin_data)/256)):
            #    for x in range((i*16) + 1,(i*16) + 16):
            #        temp = []
            #        for y in range(16):
            #            temp.append(bin_data[(x*16) + y])
            #        print(temp)

            target.append(format_man_dist(i))

            temp.append(bin_data)

            data = f.read(8)
            counter += 1

        # Train the network.

        model.fit(np.array(temp), np.array(target), epochs=5, batch_size=100)
        #model.train_on_batch(np.array(temp), np.array(target))

In [ ]:
# Used for testing data

with open('data/18.bin', 'rb') as f:
    
    for i in range(300):
        data = f.read(8)
        
    data = f.read(8)
    
    counter = 0
        
    temp = []
    
    target = []
    
    while(data):
        bin_data = reduce(format_input, list(data), [])
        bin_data.reverse()
        bin_data = bin_data[16:]

        pos_data = reduce(format_pos, enumerate(list(data)), [])
        pos_data.reverse()
        pos_data = pos_data[16:]

        target_pos = reduce(generate_pos, pos_data, [])

        #for i in range(int(len(bin_data)/256)):
        #    for x in range((i*16) + 1,(i*16) + 16):
        #        temp = []
        #        for y in range(16):
        #            temp.append(bin_data[(x*16) + y])
        #        print(temp)

        target.append(format_man_dist(target_pos))

        temp.append(bin_data)
        
        counter += 1
        data = f.read(8)

In [ ]:
# Evaluate accuracy
    
loss_and_metrics = model.evaluate(np.array(temp),np.array(target), batch_size=1000)
        
# Generating predictions:
    
predictions = model.predict(np.array(temp), batch_size=1000)

In [ ]:
output = []

for p in predictions:
    output.append(np.argmax(p))
    
print(np.array(output).mean())

print(loss_and_metrics)

print(model.metrics_names)